In [1]:
import os
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px
import numpy as np

### Select video

In [23]:
VIDEO_PATH = os.path.join("..", "..", "..", "data", "processed", "silesian_deception", "poli3Video_person3_8.npy")
SELECTED_VIDEO = np.load(VIDEO_PATH, allow_pickle=True)

In [24]:
SELECTED_LANDMARKS = [
    33, 161, 159, 157, 133, 154, 145, 163,  # left eye
    362, 384, 386, 388, 263, 390, 374, 381,  # right eye
    468, 469, 470, 471, 472, 473, 474, 475, 476, 477, # irises
]

In [25]:
SELECTED_VIDEO = SELECTED_VIDEO[:, SELECTED_LANDMARKS, :]

## Display

In [26]:
# Assuming SELECTED_VIDEO has shape (1100, 478, 2)
num_frames, num_landmarks, _ = SELECTED_VIDEO.shape

# Create a color scale - one color per landmark
color_scale = px.colors.qualitative.Alphabet  # Using a larger color palette
landmark_colors = {i: color_scale[i % len(color_scale)] for i in range(num_landmarks)}

# Initialize figure with 3D and 2D subplots
fig = make_subplots(
    rows=1, cols=2,
    specs=[[{'type': 'scatter3d'}, {'type': 'scatter'}]],
    subplot_titles=("3D Landmark Animation", "2D Landmark Positions")
)

# Add 3D scatter traces for each landmark
for landmark_idx in range(num_landmarks):
    # Get all coordinates for this landmark across frames
    x_coords = SELECTED_VIDEO[:, landmark_idx, 0]  # X coordinates
    y_coords = 1 - SELECTED_VIDEO[:, landmark_idx, 1]  # Flip Y axis for visualization
    frame_numbers = np.arange(num_frames) + 1  # Time axis
    
    fig.add_trace(
        go.Scatter3d(
            x=x_coords,
            y=frame_numbers,
            z=y_coords,
            mode='lines',
            name=f'Landmark {landmark_idx}',
            line=dict(color=landmark_colors[landmark_idx], width=2)
        ),
        row=1, col=1
    )

# Prepare frames for animation
frames = []
for t in range(num_frames):
    # Create a moving time plane
    plane_z = np.array([[0, 1], [0, 1]])
    plane_x = np.array([[0, 0], [1, 1]])
    plane_y = np.full_like(plane_x, t+1)  # Plane position matches current frame
    
    plane = go.Surface(
        z=plane_z,
        x=plane_x,
        y=plane_y,
        surfacecolor=np.full_like(plane_x, 0.5),
        colorscale=[[0, "grey"], [1, "grey"]],
        opacity=0.5,
        showscale=False,
        name="Time Plane"
    )
    
    # Get current frame's landmarks
    current_frame = SELECTED_VIDEO[t]
    x_coords = current_frame[:, 0]
    y_coords = 1 - current_frame[:, 1]  # Flip Y
    
    # Create scatter plot for current frame
    scatter = go.Scatter(
        x=x_coords,
        y=y_coords,
        mode='markers',
        marker=dict(
            size=6,
            color=[landmark_colors[i] for i in range(num_landmarks)],
            opacity=1
        ),
        name=f'Frame {t+1}'
    )
    
    frames.append(go.Frame(
        data=[plane, scatter],
        name=str(t+1)
    ))

# Add frames and animation controls
fig.frames = frames

# Update layout
fig.update_layout(
    height=800,
    scene=dict(
        xaxis_title='X coord',
        yaxis_title='Frame Number',
        zaxis_title='Y coord',
        xaxis=dict(range=[0, 1]),
        yaxis=dict(range=[1, num_frames]),
        zaxis=dict(range=[0, 1]),
    ),
    sliders=[{
        "steps": [{
            "args": [
                [str(t+1)],
                {
                    "frame": {"duration": 50, "redraw": True},
                    "mode": "immediate",
                    "transition": {"duration": 50}
                }
            ],
            "label": f"Frame {t+1}",
            "method": "animate"
        } for t in range(num_frames)],
        "currentvalue": {"prefix": "Frame: ", "visible": True, "xanchor": "center"},
    }],
    title="Landmark Positions Over Time",
    margin=dict(l=0, r=0, b=0, t=40),
    xaxis=dict(range=[0, 1], title="X coord"),
    yaxis=dict(range=[0, 1], title="Y coord")
)

# Add play/pause button
fig.update_layout(
    updatemenus=[{
        "type": "buttons",
        "buttons": [
            {
                "args": [None, {"frame": {"duration": 50, "redraw": True},
                          "fromcurrent": True, "transition": {"duration": 50}}],
                "label": "Play",
                "method": "animate"
            },
            {
                "args": [[None], {"frame": {"duration": 0, "redraw": True},
                          "mode": "immediate", "transition": {"duration": 0}}],
                "label": "Pause",
                "method": "animate"
            }
        ],
        "x": 1,
        "y": 0,
    }]
)

fig.show()

In [10]:
import cv2
import mediapipe as mp
import numpy as np
import time

mp_face_mesh = mp.solutions.face_mesh
face_mesh = mp_face_mesh.FaceMesh(refine_landmarks=True)

EYE_LANDMARKS = {
    "left": {
        "outer": 33,
        "inner": 133,
        "top": 159,
        "bottom": 145,
        "iris_center": 468
    },
    "right": {
        "outer": 263,
        "inner": 362,
        "top": 386,
        "bottom": 374,
        "iris_center": 473
    }
}
# cap = cv2.VideoCapture(os.path.join('..', '..', '..', 'data', 'raw', 'silesian_deception_cut', 'poli1Video', 'person3_7.avi'))
cap = cv2.VideoCapture('eye_movement.mp4')
frame_rate = cap.get(cv2.CAP_PROP_FPS)

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
    results = face_mesh.process(rgb)

    if results.multi_face_landmarks:
        landmarks = results.multi_face_landmarks[0].landmark
        h, w, _ = frame.shape

        def lm(id):
            pt = landmarks[id]
            return np.array([pt.x * w, pt.y * h])

        is_blinking = True
        directions = np.zeros((2, 2))

        for i, eye in enumerate(['left', 'right']):
            # Get eye and iris points
            eye_outer = lm(EYE_LANDMARKS[eye]['outer'])
            eye_inner = lm(EYE_LANDMARKS[eye]['inner'])
            top_lid = lm(EYE_LANDMARKS[eye]['top'])
            bottom_lid = lm(EYE_LANDMARKS[eye]['bottom'])

            cv2.circle(frame, tuple(eye_outer.astype(int)), 3, (255, 0, 0), -1)
            cv2.circle(frame, tuple(eye_inner.astype(int)), 3, (255, 0, 0), -1)
            eye_center = (eye_outer + eye_inner) / 2
            iris_center = lm(EYE_LANDMARKS[eye]['iris_center'])
            direction_vector = iris_center - eye_center

            cv2.circle(frame, tuple(iris_center.astype(int)), 3, (0, 255, 255), -1)
            cv2.circle(frame, tuple(eye_center.astype(int)), 3, (255, 255, 255), -1)

            # Normalize: divide by eye width to make scale-independent
            eye_width = np.linalg.norm(eye_outer - eye_inner)
            directions[i] = direction_vector / (eye_width / 2 )

            # detect blinking
            eye_width = np.linalg.norm(eye_outer - eye_inner)
            eye_opening = np.linalg.norm(top_lid - bottom_lid)
            eye_ratio = eye_opening / eye_width
            is_blinking = is_blinking and eye_ratio < 0.2
        
        # Display
        cv2.putText(frame, f"Direction: {np.mean(directions, axis=0).round(2)}", (30, 30),
                    cv2.FONT_HERSHEY_SIMPLEX, 0.7, (255, 0, 0), 2)
        cv2.putText(frame, f"Blinking: {is_blinking}", (30, 60),
                    cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0, 0, 255) if is_blinking else (0, 255, 0), 2)

        time.sleep(0.1)

    cv2.imshow('Eye Tracking', frame)
    if cv2.waitKey(1) & 0xFF == 27:
        break

cap.release()
cv2.destroyAllWindows()


C:\Users\Bartosz\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\google\protobuf\symbol_database.py:55: UserWarning: SymbolDatabase.GetPrototype() is deprecated. Please use message_factory.GetMessageClass() instead. SymbolDatabase.GetPrototype() will be removed soon.
  warnings.warn('SymbolDatabase.GetPrototype() is deprecated. Please '
